Librosa Test

In [1]:
import os
import numpy as np
import librosa
import librosa.display 
import IPython.display as ipd 
%matplotlib inline 
import matplotlib.pyplot as plt

In [10]:
dir_path = './Data'

In [122]:
ex1 = 'ex1_Wake Me Up.mp3'
ex2 = 'ex2_HONEY.mp3'
ex3 = 'ex3_Business.mp3'

In [123]:
audio_path = os.path.join(dir_path, ex1) # ex1, ex2 or ex3

In [124]:
ipd.Audio(audio_path)

In [ ]:
y , sr = librosa.load(audio_path) 
print(type(y), type(sr)) 
print(y.shape, sr)

<class 'numpy.ndarray'> <class 'int'>
(5505984,) 22050


In [ ]:
plt.figure(figsize=(14, 5)) 
librosa.display.waveplot(y, sr=sr)

In [ ]:
Y = librosa.stft(y)
Ydb = librosa.amplitude_to_db(abs(Y))
plt.figure(figsize=(14,5))
librosa.display.specshow(Ydb,sr=sr,x_axis='time',y_axis='hz')
plt.colorbar()

In [ ]:
librosa.display.specshow(Ydb, sr = sr, x_axis = 'time', y_axis = 'log') 
plt.colorbar()

In [ ]:
hop_length = 512 
chromagram = librosa.feature.chroma_stft(y, sr=sr, hop_length=hop_length) 
plt.figure(figsize=(15, 5))
librosa.display.specshow(chromagram, x_axis='time', y_axis='chroma', hop_length=hop_length, cmap='coolwarm')

In [ ]:
S_full, phase = librosa.magphase(librosa.stft(y))
idx = slice(*librosa.time_to_frames([30, 35], sr=sr))
plt.figure(figsize=(12, 4))
librosa.display.specshow(librosa.amplitude_to_db(S_full[:, idx], ref=np.max),
                         y_axis='log', x_axis='time', sr=sr)
plt.colorbar()
plt.tight_layout()

In [ ]:
S_filter = librosa.decompose.nn_filter(S_full,
                                       aggregate=np.median,
                                       metric='cosine',
                                       width=int(librosa.time_to_frames(2, sr=sr)))

In [ ]:
S_filter = np.minimum(S_full, S_filter)

In [ ]:
# We can also use a margin to reduce bleed between the vocals and instrumentation masks.
# Note: the margins need not be equal for foreground and background separation
margin_i, margin_v = 2, 10
power = 2

mask_i = librosa.util.softmask(S_filter,
                               margin_i * (S_full - S_filter),
                               power=power)

mask_v = librosa.util.softmask(S_full - S_filter,
                               margin_v * S_filter,
                               power=power)

# Once we have the masks, simply multiply them with the input spectrum
# to separate the components

S_foreground = mask_v * S_full
S_background = mask_i * S_full

In [ ]:
# sphinx_gallery_thumbnail_number = 2

plt.figure(figsize=(12, 8))
plt.subplot(3, 1, 1)
librosa.display.specshow(librosa.amplitude_to_db(S_full[:, idx], ref=np.max),
                         y_axis='log', sr=sr)
plt.title('Full spectrum')
plt.colorbar()

plt.subplot(3, 1, 2)
librosa.display.specshow(librosa.amplitude_to_db(S_background[:, idx], ref=np.max),
                         y_axis='log', sr=sr)
plt.title('Background')
plt.colorbar()
plt.subplot(3, 1, 3)
librosa.display.specshow(librosa.amplitude_to_db(S_foreground[:, idx], ref=np.max),
                         y_axis='log', x_axis='time', sr=sr)
plt.title('Foreground')
plt.colorbar()
plt.tight_layout()
plt.show()

In [ ]:
name, ext = os.path.splitext(audio_path)
output_file_path = name + '_vocal.wav'

In [ ]:
D_foreground = S_foreground * phase
y_foreground = librosa.istft(D_foreground)

In [ ]:
librosa.output.write_wav(output_file_path, y_foreground, sr)

In [ ]:
ipd.Audio(output_file_path)

SpotiPy Test

In [ ]:
import spotipy
import json
import pandas as pd
import matplotlib.pyplot as plt
from spotipy.oauth2 import SpotifyClientCredentials

In [ ]:
# Spotify API Preparation
client_id = 'client id'  # Replace this with your client id
client_secret = 'client secret'  # Replace this with your client secret
client_credentials_manager = spotipy.oauth2.SpotifyClientCredentials(client_id, client_secret)
spotify = spotipy.Spotify(client_credentials_manager=client_credentials_manager)

In [ ]:
# define a dataFrame to store artist info
artist_df = pd.DataFrame(columns=['artist_name','artist_ID','genre','popularity','related_artist_names'])

In [ ]:
# Retrieve info of an artist
name = 'ONE OK ROCK'
spotapi_out = spotify.search(q='artist:' + name, type='artist')
artist_items = spotapi_out['artists']['items'][0]
artist_id = artist_items['id']
artid_list = [artist_id]
artname_related_list = []
spotapi_out_related = spotify.artist_related_artists(artist_id)
for artname_related in spotapi_out_related['artists']:
    artname_related_list.append(artname_related['name'])
s = pd.Series([artist_items['name'], artist_items['id'], artist_items['genres'],artist_items['popularity'],artname_related_list],index=artist_df.columns)
artist_df = artist_df.append(s,ignore_index=True)

In [ ]:
spotapi_out